In [ ]:
!pip install xformers
!pip install numpy==1.23.3


In [ ]:
import pandas as pd
import numpy as np
import scipy as sp
import torch
import transformers
import shap
import xformers
from transformers import BertTokenizer, BertForSequenceClassification

In [5]:
test_data = pd.read_csv("data/test_new.csv")

# Converting bools to binary
test_data["labels"] = test_data["labels"].astype(int)

idx = 43 # choose an index of the article to read
x = [test_data["text"][idx]]

In [6]:
# Load the BERT tokenizer.
print('Loading BERT tokenizer...')
tokenizer = BertTokenizer.from_pretrained('chcaa/dfm-encoder-large-v1', do_lower_case=True)
tokenizer.model_max_length = 512
tokenizer.max_length = 512
tokenizer.truncation = True

Loading BERT tokenizer...


In [20]:
model = BertForSequenceClassification.from_pretrained('model', num_labels=2)

pipe = transformers.pipeline("text-classification", model=model, tokenizer=tokenizer, top_k=None, padding=True, truncation=True, max_length = 512) # , padding=True, truncation=True

pred = pipe(x, padding=True, truncation=True, max_length = 512)

In [21]:
print(pred) # print prediction probabilities

[[{'label': 'LABEL_0', 'score': 0.7044879198074341}, {'label': 'LABEL_1', 'score': 0.2955121099948883}]]


In [ ]:
print(test_data['text'][32]) # read the article

In [23]:
# Create an explainer for the pipeline
explainer = shap.Explainer(pipe)

# Compute SHAP values
shap_values = explainer(x)

# Visualize the impact on all the output classes
shap.plots.text(shap_values)